In [ ]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from plotly.offline import init_notebook_mode, iplot, plot
import plotly as py
init_notebook_mode(connected=True)
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objs as go
import matplotlib.pyplot as plt
from plotly.subplots import make_subplots
from scipy.stats import pearsonr
from scipy.stats import spearmanr
import os

In [ ]:
def configure_plotly_browser_state():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              plotly: 'https://cdn.plot.ly/plotly-latest.min.js?noext',
            },
          });
        </script>
        '''))

configure_plotly_browser_state()

# Требования: 
- во всех графиках должны быть подписи чере title, legend, etc... 
- Убедитесь, что после сохранения ноутбука графики всё ещё видно, если открыть ноутбук заново, если не видно, то напишите мне @kirizhik 
- Можно баловаться с цветами, чтобы было **K P A C U B O**, но **не вырвеглазно**, пожалуйста

In [ ]:
df = pd.read_csv('data.csv', index_col = 0)

In [ ]:
df.columns

Index(['ID', 'Name', 'Age', 'Photo', 'Nationality', 'Flag', 'Overall',
       'Potential', 'Club', 'Club Logo', 'Value', 'Wage', 'Special',
       'Preferred Foot', 'International Reputation', 'Weak Foot',
       'Skill Moves', 'Work Rate', 'Body Type', 'Real Face', 'Position',
       'Jersey Number', 'Joined', 'Loaned From', 'Contract Valid Until',
       'Height', 'Weight', 'LS', 'ST', 'RS', 'LW', 'LF', 'CF', 'RF', 'RW',
       'LAM', 'CAM', 'RAM', 'LM', 'LCM', 'CM', 'RCM', 'RM', 'LWB', 'LDM',
       'CDM', 'RDM', 'RWB', 'LB', 'LCB', 'CB', 'RCB', 'RB', 'Crossing',
       'Finishing', 'HeadingAccuracy', 'ShortPassing', 'Volleys', 'Dribbling',
       'Curve', 'FKAccuracy', 'LongPassing', 'BallControl', 'Acceleration',
       'SprintSpeed', 'Agility', 'Reactions', 'Balance', 'ShotPower',
       'Jumping', 'Stamina', 'Strength', 'LongShots', 'Aggression',
       'Interceptions', 'Positioning', 'Vision', 'Penalties', 'Composure',
       'Marking', 'StandingTackle', 'SlidingTackle', 'GKDiv

In [ ]:
df[['Wage']].head(10)

Wage
0  €565K
1  €405K
2  €290K
3  €260K
4  €355K
5  €340K
6  €420K
7  €455K
8  €380K
9   €94K

In [ ]:
df.dtypes.value_counts()

object     45
float64    38
int64       5
dtype: int64

In [ ]:
# Выполнения заданий ниже (можно было бы и из info выписать, но не хочу)
n_features = df.shape[1]
print("Количество признаков: ", n_features)
print("Числовых признаков: ", n_features - df.dtypes.value_counts()[0])

Количество признаков:  88
Числовых признаков:  43


In [ ]:
def make_numeric_value(x: str) -> float:
  x = x[1:]
  val = x[-1]
  if (val == 'K'):
    x = float(x[:len(x) - 1]) * 1000
  elif (val == 'M'):
    x = float(x[:len(x) - 1]) * 1000000
  return x

Предобработаем четыре признака

In [ ]:
df['Value'] = df['Value'].apply(make_numeric_value).astype(float)

In [ ]:
df['Wage'] = df['Wage'].apply(make_numeric_value).astype(float)

In [ ]:
df['Contract Valid Until'] = df['Contract Valid Until'].astype(str).apply(lambda x: x.split()[-1])

In [ ]:
df['Joined'] = df['Joined'].astype(str).apply(lambda x: x.split()[-1])

# Заполните пропуски в утверждениях 

- В датасете -- 88 переменных 

- Из них числовых -- 43

# Изучите распределение возростов с помощью Age [px.histogram](https://plotly.com/python/histograms/), изучите [более продвинутые методы](https://plotly.com/python/distplot/) визуализации распределений 

In [ ]:
# Ваш код красивый и самый лучший сюда
configure_plotly_browser_state()
fig = ff.create_distplot([df['Age']], ['Возраст'], bin_size=1, show_rug=False, histnorm="probability density")
fig.update_layout(title_text='Распределение возрастов игроков, представленных в FIFA')
fig.update_xaxes(title_text='Возраст игроков')
fig.update_yaxes(title_text="Доля игроков этого возраста")
fig.update_layout(font_size = 16)
fig.show()

# Мои выводы по распределению
Можно заметить, что плотность распределения растёт, достигает пикового значения при значении 21 года, затем стагнирует до 26 лет, а затем резко падает.

Это немного противоречит с тем, что принято считать, что к пику карьеры футболисты подходят к 28-32 годам. У меня есть две гипотезы, почему так происходит:
1. Обойма команды обычно состоит из 15-17 игроков, из которых и так 1-2 --- молодые ребята. Но в FIFA обычно список футболистов команды состоит из 20-25 человек, соответственно, в каждом клубе есть куча спортсменов, добавленных из молодёжных/резервных составов, поэтому распределение сдвинуто в сторону от пикового значения физических кондиций игрока. (причина в самой FIFA)

2. Из футбольных академий выпускается много человек, каждый из которых считается перспективным. Но затем часть игроков получают тяжёлые травмы, кто-то не оправдывает надежд, кто-то сам разочаровывается от футбола. Поэтому из молодняка не так много футболистов продолжают свою профессиональную карьеру до 30 лет. (причина в реальном положении в футболе).



---



---



---



# Визуализируйте соотношенеие между левшами и правшами (? сами найдите необходимую колонку в данных, считаем, что левша-правша ~ предпочтительная нога для ударов )

В наших данных за колонку предпочитаемой ноги отвечает Preferred Foot.

Я решил добавить к визуализацию также распределение левшей-правшей среди обычных людей, взяв просто статистические данные (% от всех людей), а затем визуализировать это другим цветом. 

У меня есть гипотеза, что доля левшей среди футболистов будет больше, чем среди обычных людей.

In [ ]:
N = df["Preferred Foot"].shape[0]
percent = 0.102
real_people = np.array(["Left"] * int(N * percent) + ["Right"] * int(N * (1 - percent)))
real_people = pd.DataFrame(real_people, columns = ["Preferred Foot"])

In [ ]:
real_people.shape[0]
df["Preferred Foot"].shape[0]

18207

In [ ]:
fig = go.Figure()
fig.add_trace(go.Histogram(x=df["Preferred Foot"], name = "Футболисты", histnorm = "probability"))
fig.add_trace(go.Histogram(x=real_people["Preferred Foot"], name = "В целом по человечеству", histnorm = "probability"))
fig.update_xaxes(title_text="Предпочитаемая нога")
fig.update_yaxes(title_text="Доля людей с такой ногой")
fig.update_layout(font_size = 16)
fig.update_layout(title_text = "Распределение правшей-левшей")
configure_plotly_browser_state()
fig.show()

# Мои выводы по распределению
Гипотеза подтвердилось, и доля левшей среди футболистов в два раза больше, чем среди обычных людей. Хотя, конечно, правши доминируют (их больше в три раза), но доля от общечеловеческой отличается.

Это можно объяснить тем, в детском футболе чаще всего на левом фланге играет минимум два игрока, поэтому тренера охотнее берут и развивают левшей (по крайней мере в то время, когда я играл, у левшей действительно было небольшое преимущество в этом плане), у них больше игровой практики. Два игрока - это минимум 18% всех футболистов, отсюда и разница среди реальных футболистов.



---



---



---



# Визуализируйте Международный Рейтинг футболистов (International Reputation), ассоциирован ли он с национальностью? футбольным клубом? 


Колонка национальности: 'Nationality'

Колонка футбольного клуба: 'Club'

In [ ]:
# ну сами понимаете...
fig = go.Figure()
fig.add_trace(go.Histogram(x=df["International Reputation"], name = "Репутация"))
fig.update_xaxes(title_text="Международный рейтинг")
fig.update_yaxes(title_text="Количество игроков с таким рейтингом")
fig.update_layout(font_size = 16)
fig.update_layout(title_text = "Распределение международного рейтинга футболистов")
configure_plotly_browser_state()
fig.update_layout(width=1300, height=800)
fig.show()

# Мои выводы по распределению
Большинство футболистов -- имеет международный рейтинг равный единице. Всего 1500 игроков по всему миру имеют рейтинг больше, чем один.


---



In [ ]:
df_club_rep = df[['Nationality', 'International Reputation']].groupby('Nationality').agg('mean').\
                                                              sort_values(by = 'International Reputation', 
                                                                          ascending = False)
df_club_rep = df_club_rep.iloc[:20][::-1]

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_club_rep.index,
    x=df_club_rep['International Reputation'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_club_rep['International Reputation'],
    orientation='h'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Топ-20 лучших стран по средней международной репутации')
fig.update_xaxes(title_text='Среднее значение международной репутации')
fig.update_yaxes(title_text="Страна")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1500, height=800)
fig.show()

# Мои выводы по распределению
Самый высокий средний рейтинг имеют страны, которые нельзя назвать футбольными: Оман, Бурунди, ОАЭ, Того. Такой результат связан с тем, что из этих стран только один-два человека представлены в FIFA, то есть это уровень главных звёзд страны. И поэтому так совпало, что у них большой средний рейтинг.


И если взять Россию, то мы находимся выше, чем Англия, хотя у нас очень мало игроков, о которых что-то знают в Европе (на момент FIFA 2019 это Черышев, Головин, Дзюба, Игнашевич, Акинфеев). Просто у нас представлена только сборная, а обычные игроки не рассматриваются.

Футбольные страны вроде Франции имеют рейтинг меньше, чем 1.33, что говорит о том, что в основном из этих стран международный рейтинг все равно равен единице. 

Поэтому можно утверждать, что связь между национальностью и международным рейтингом отсутствует: международный рейтинг определяется только достижениями самого игрока. Единственная возможная связь: в более развитых в футбольном плане странах средний рейтинг чуть повыше, но для конкретного игрока нет никакой разницы, какой он национальности.


---



In [ ]:
df_club_rep = df[['Club', 'International Reputation']].groupby('Club').agg('mean').\
                                                              sort_values(by = 'International Reputation', 
                                                                          ascending = False)
df_club_rep = df_club_rep.iloc[:20][::-1]

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_club_rep.index,
    x=df_club_rep['International Reputation'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_club_rep['International Reputation'],
    orientation='h'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Топ-20 лучших клубов по средней международной репутации')
fig.update_xaxes(title_text='Среднее значение международной репутации')
fig.update_yaxes(title_text="Клуб")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1500, height=800)
fig.show()

# Мои выводы по распределению
В топ-клубах действительно средний рейтинг выше, чем в обычных клубах. Это связано с тем, что неплохой игрой в топ-клубе футболиста узнают гораздо лучше, чем если он отлично играет в каком-нибудь середняке. Плюс, топ-клубы откровенный шлак не берут (Барселона и Спартак не считаются), поэтому появление в топ-клубе явно повлияет на международный рейтинг.



---



---



---



# Есть ли зависимость между потенциалом (Potential) и Международным Рейтингом футболистов (International Reputation)? Визуализируте её. Влияет ли на потенциал игровая нога? Почему так может случиться? (картинка в тему)

![Коазуация или корреляция?](causuation.png "???")

In [ ]:
df_pi = df[['Potential', 'International Reputation']].dropna()
corr = spearmanr(df_pi['Potential'], df_pi['International Reputation'])
print("Значение корреляции Спирмена между потенциалом и международной репутацией: {}".format(corr[0]))

Значение корреляции Спирмена между потенциалом и международной репутацией: 0.3203586948356044


In [ ]:
df_pot_rep = df[['Potential', 'International Reputation']].groupby('Potential').agg('mean').\
                                                              sort_values(by = 'International Reputation', 
                                                                          ascending = False)

fig = go.Figure()
fig.add_trace(go.Bar(
    x=df_pot_rep.index,
    y=df_pot_rep['International Reputation'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_pot_rep['International Reputation'],
    orientation='v'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Зависимость международного рейтинга от потенциала')
fig.update_xaxes(title_text='Потенциал')
fig.update_yaxes(title_text="Средний международный рейтинг")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1500, height=800)
fig.show()

# Мои выводы по распределению

У игроков с большим потенциалом в среднем больше международный рейтинг. Но тут скорее зависимость другая: у игроков 25+ как правило текущий рейтинг примерно равен потенциалу, так как чем сильнее игрок, тем выше его международная репутация. Напрямую потенциал не влияет, но статистическая корреляция есть (что видно по корреляции) - коазуация, получается. 


---



In [ ]:
df_foot_rep = df[['Preferred Foot', 'Potential']].groupby('Preferred Foot').agg('mean').\
                                                              sort_values(by = 'Potential', 
                                                                          ascending = False)

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_foot_rep.index,
    x=df_foot_rep['Potential'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_foot_rep['Potential'],
    orientation='h'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Зависимость потенциала от ведущей ноги')
fig.update_xaxes(title_text='Средний потенциал')
fig.update_yaxes(title_text="Ведущая нога")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1000, height=400)
fig.show()

# Мои выводы по распределению
Зависимости между потенциалом и ведущей ногой нет. В среднем всё распределено одинаково.



---



---



# Теперь пройдёмся по показателям игроков... 
### Есть ли зависимость Выносливости (Stamina) и Силы (Strength) игроков? какая? точно зависимость? 


In [ ]:
df_cop = df.copy(deep = True)[['Stamina', 'Strength']].dropna()[:1000]
corr = spearmanr(df_cop['Stamina'], df_cop['Strength'])
print("Значение корреляции Спирмена между силой и выносливостью: {}".format(corr[0]))

Значение корреляции Спирмена между силой и выносливостью: 0.016471712124170458


In [ ]:
fig = go.Figure(data=go.Scatter(x=df_cop['Stamina'], y= df_cop['Strength'], mode='markers'))
fig.update_layout(title_text = "Распределение характеристик силы и выносливости")
fig.update_xaxes(title_text="Показатель выносливости")
fig.update_yaxes(title_text="Показатель силы")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
configure_plotly_browser_state()
fig.show()

# Мои выводы по распределению
В основном у игроков сила распределена в интервале 55-80.

На рисунке видно два кластера: один с игроками с ужасной выносливостью (скорее всего, это вратари и очень старые игроки), другой - с игроками с гармоничным физическим развитием.

Прямой зависимости тут точно не может быть, несмотря на некоторую статистическую зависимость, так как, во-первых, это разные физические параметры по растянутости по времени, во-вторых, у них, скорее, есть другие формирующие их признаки (возраст, общие природные данные).



---



---



---



# Зависит ли Стоимость игрока стоимость (Value) игрока от его "финтов" (Skill Moves)? 

In [ ]:
df_cop = df.copy(deep = True)[['Value', 'Skill Moves']].dropna()
corr = spearmanr(df_cop['Value'], df_cop['Skill Moves'])
print("Значение корреляции Спирмена стоимости игрока от его финтов: {}".format(corr[0]))

Значение корреляции Спирмена стоимости игрока от его финтов: 0.4920078377693975


In [ ]:
df_cop['Skill Moves'].value_counts()

2.0    8565
3.0    6600
1.0    2026
4.0     917
5.0      51
Name: Skill Moves, dtype: int64

In [ ]:
fig = go.Figure()

x = np.arange(1, 6, 1)
for el in x:
  fig.add_trace(go.Box(y=df_cop[df_cop['Skill Moves'] == el]['Value'], name = "Уровень дриблинга - {}".format(el)))

configure_plotly_browser_state()
fig.update_layout(title_text= 'Зависимость стоимости игрока от его дриблинга')
fig.update_xaxes(title_text='Уровень дриблинга')
fig.update_yaxes(title_text="Распределение стоимости")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы по распределению
У игроков с высоким уровнем дриблинга действительно выше медианная цена, но при этом видно, что вверх выбросы есть во всех категориях. Так что однозначно дриблинг оказывает влияние на цену, но не ключевое.



---



---


# Покажите распределеняи основных характеристик игроков: Рост, Вес, Возраст по позициям (Position), сделайте выводы...


In [ ]:
# Предобработаем вес, рост

def height_to_sm(x):
    string = x.split("'")
    return float(string[0]) * 30.48 + float(string[1]) * 2.54

def weight_to_sm(x):
    string = x[:len(x) - 3]
    return float(string) * 0.453592

df_dist = pd.DataFrame(columns = ['Age', 'Weight', 'Height'], index=df['Position'].value_counts().index)

for pos in df_dist.index:
  df_dist.loc[pos, 'Age'] = df[df['Position'] == pos]['Age'].mean()
  df_dist.loc[pos, 'Weight'] = df[df['Position'] == pos]['Weight'].dropna().astype(str).apply(weight_to_sm).mean()
  df_dist.loc[pos, 'Height'] = df[df['Position'] == pos]['Height'].dropna().astype(str).apply(height_to_sm).mean()

In [ ]:
df_dist.sort_values(by = 'Height', ascending=True, inplace=True)

mask1 = df_dist['Height'] >= 182
mask2 = (df_dist['Height'] > 177) & (df_dist['Height'] < 182)
mask3 = df_dist['Height'] <= 177

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_dist['Height'][mask3],
    x=df_dist[mask3].index,
    marker_color = 'lime',
    name = "'Низкие' позиции (<=177см)",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Height'][mask2],
    x=df_dist[mask2].index,
    marker_color = 'blue',
    name = "'Средние' позиции",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Height'][mask1],
    x=df_dist[mask1].index,
    marker_color = 'red',
    name = "'Высокие' позиции (>=182см)",
    orientation = 'v'
))
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость роста игрока от его позиции на поле")
fig.update_xaxes(title_text="Позиция игрока")
fig.update_yaxes(title_text="Средний рост по позиции (см)")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы по распределению
Самыми высокими оказались позиции, требующие игры в воздухе: вратарь, центральные защитники и нападающие. 

Самые низкими оказались игроки, которые наоборот в основном владеют мячом внизу: крайние полузащитники, крайние нападающие, ЦАП.

Здесь всё логично.


---


In [ ]:
df_dist.sort_values(by = 'Weight', ascending=True, inplace=True)

mask1 = df_dist['Weight'] >= 77
mask2 = (df_dist['Weight'] > 72) & (df_dist['Weight'] < 77)
mask3 = df_dist['Weight'] <= 72

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_dist['Weight'][mask3],
    x=df_dist[mask3].index,
    marker_color = 'lime',
    name = "'Лёгкие' позиции (<= 72кг)",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Weight'][mask2],
    x=df_dist[mask2].index,
    marker_color = 'blue',
    name = "'Средние' позиции",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Weight'][mask1],
    x=df_dist[mask1].index,
    marker_color = 'red',
    name = "'Тяжёлые' позиции (>=77кг)",
    orientation = 'v'
))
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость веса игрока от его позиции на поле")
fig.update_xaxes(title_text="Позиция игрока")
fig.update_yaxes(title_text="Средний вес по позиции (в кг)")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы по распределению
Получилось похожее распределение, что и с ростом, что логично - чем выше человек, тем больше его рост. Так как футболисты редко страдают ожирением, и в среднем все примерно с одинаковым процентом жира, то и получился график, который отличается от графика роста лишь в деталях.



---


In [ ]:
df_dist.sort_values(by = 'Age', ascending=True, inplace=True)

mask1 = df_dist['Age'] >= 26
mask2 = (df_dist['Age'] > 24) & (df_dist['Age'] < 26)
mask3 = df_dist['Age'] <= 24

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_dist['Age'][mask3],
    x=df_dist[mask3].index,
    marker_color = 'lime',
    name = "'Молодые' позиции (<= 24)",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Age'][mask2],
    x=df_dist[mask2].index,
    marker_color = 'blue',
    name = "'Средние' позиции",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_dist['Age'][mask1],
    x=df_dist[mask1].index,
    marker_color = 'red',
    name = "'Старые' позиции (>=26)",
    orientation = 'v'
))
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость возраста игрока от его позиции на поле")
fig.update_xaxes(title_text="Позиция игрока")
fig.update_yaxes(title_text="Средний возраст по позиции")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы по распределению

А вот тут шок для меня. То, что центральные игроки оказались в топе, как и вратарь - это логично, так как от них не требуется в такой степени резкость и скорость, как от нападающих. А она напрямую зависит от возраста. Но на первых местах в топе есть крайние атакующие игроки (LAM, RAM, RF). А ещё в топе LCB и RCB, в то время как для CB и CAM находятся в середине (хотя по сути это одни и те же позиции).

Скорее всего, это связано с особенностью данных и редкостью этих позиций, и как следствие, малое количество молодых игроков, которым ставят дефолтные LM, RM, CAM и CB.



---



---

# Есть ли зависимость скорости (SprintSpeed) от веса и роста? А от национальности?  

In [ ]:
df_cop = df.copy(deep = True)[['Weight', 'SprintSpeed', 'Height']].dropna()
corr = spearmanr(df_cop['Weight'], df_cop['SprintSpeed'])
print("Значение корреляции Спирмена между весом и скоростью: {}".format(corr[0]))

Значение корреляции Спирмена между весом и скоростью: -0.392667681709502


In [ ]:
df_cop = df.copy(deep = True)[['Weight', 'SprintSpeed', 'Height']].dropna()
corr = spearmanr(df_cop['Height'], df_cop['SprintSpeed'])
print("Значение корреляции Спирмена между ростом и скоростью: {}".format(corr[0]))

Значение корреляции Спирмена между ростом и скоростью: -0.39501390367378686


In [ ]:
# Предобработаем вес, рост

def height_to_sm(x: str) -> float:
    string = x.split("'")
    return float(string[0]) * 30.48 + float(string[1]) * 2.54

def weight_to_sm(x: str) -> float:
    string = x[:len(x) - 3]
    return float(string) * 0.453592

In [ ]:
df_cop['Weight'] = df_cop['Weight'].dropna().astype(str).apply(weight_to_sm).astype(int)
df_cop['Height'] = df_cop['Height'].dropna().astype(str).apply(height_to_sm).astype(int)

In [ ]:
df_weight = df_cop.groupby('Weight').agg({'SprintSpeed':'mean'})
fig = px.scatter(df_weight, x= df_weight.index, y="SprintSpeed", trendline="lowess", size = [1.5] * 46)

configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость скорости от веса игрока")
fig.update_xaxes(title_text="Вес игрока")
fig.update_yaxes(title_text="Средняя скорость для такого веса")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

/usr/local/lib/python3.7/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning:

pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.



# Мои выводы по распределению

Между скоростью и весом есть обратная пропорция: чем больше вес, тем меньше скорость. Это логично, и думаю, нет смысла объяснять почему.


---



---



In [ ]:
df_height = df_cop.groupby('Height').agg({'SprintSpeed':'mean'})
fig = px.scatter(df_height, x= df_height.index, y="SprintSpeed", trendline="lowess", size = [2] * 21)
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость скорости от высоты игрока")
fig.update_xaxes(title_text="Рост игрока")
fig.update_yaxes(title_text="Средняя скорость для такого роста")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()


# Мои выводы по распределению

Как уже выяснили выше, рост и вес в футболе пропорциональны друг другу, поэтому логично, что с увеличением роста падает скорость, несмотря на то, шаг вроде бы должен быть длиннее. Чем больше рост, тем больше вес, и тем менее скоординированным становится игрок




---



In [ ]:
df_nations = df.Nationality.value_counts()
df_nations = df_nations[df_nations > 50]

df_speed_country = pd.DataFrame(columns = ['SprintSpeed', 'Nationality'])
i = 0
for country in df_nations.index:
  df_speed_country.loc[i, 'SprintSpeed'] = df[df['Nationality'] == country]['SprintSpeed'].mean()
  df_speed_country.loc[i, 'Nationality'] = country
  i += 1

In [ ]:
df_speed_country.sort_values(by = 'SprintSpeed', ascending=True, inplace=True)

mask1 = df_speed_country['SprintSpeed'] >= 66
mask2 = (df_speed_country['SprintSpeed'] > 63) & (df_speed_country['SprintSpeed'] < 66)
mask3 = df_speed_country['SprintSpeed'] <= 63

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_speed_country['SprintSpeed'][mask3],
    x=df_speed_country[mask3]['Nationality'],
    marker_color = 'lime',
    name = "'Медленные' национальности (<=63)",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_speed_country['SprintSpeed'][mask2],
    x=df_speed_country[mask2]['Nationality'],
    marker_color = 'blue',
    name = "'Средние' национальности",
    orientation = 'v'
))

fig.add_trace(go.Bar(
    y=df_speed_country['SprintSpeed'][mask1],
    x=df_speed_country[mask1]['Nationality'],
    marker_color = 'red',
    name = "'Быстрые' национальности (>=66)",
    orientation = 'v'
))
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость скорости игрока от национальности")
fig.update_xaxes(title_text="Национальность игрока")
fig.update_yaxes(title_text="Средняя скорость по национальности")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы по распределению

От национальности действительно есть зависимость, связанная скорее с генетической предрасположенностью определённых наций. Например, африканцы по скорости рвут все страны, особенно Нигерия и Гана. Что логично, так как негройды в целом более физически развиты.

Также в топе латиносы, что связано с их безбашенным и скоростным стилем игры. Что забыла в топе Румыния - я не знаю.




---



---

# Под какими номерами чаще всего играют нападающие? Визуализируйте частотность  

Сначала я покажу распределение для всех позиций нападающих, а затем посмотрю на распределение самого предпочитаемого номера для каждой позиции 


In [ ]:
# давай-давай 
mask = df['Position'].apply(lambda x: x in ["ST", "LW", "RW", "CF", "RF", "LF", "LS", "RS"])
df_forward = df[mask][["Name", "Jersey Number", "Position"]]
df_forward.head()

Name  Jersey Number Position
0           L. Messi           10.0       RF
1  Cristiano Ronaldo            7.0       ST
2          Neymar Jr           10.0       LW
5          E. Hazard           10.0       LF
7          L. Suárez            9.0       RS

In [ ]:
configure_plotly_browser_state()
fig = ff.create_distplot([df_forward['Jersey Number']], ['Номер нападающего'], bin_size=1, show_rug=False, histnorm="probability density")
fig.update_layout(title_text='Распределение номеров нападающих')
fig.update_xaxes(title_text='Номера')
fig.update_yaxes(title_text="Доля номера среди нападающих")
fig.update_layout(font_size = 16)
fig.update_layout(width=1300, height=800)
fig.show()

In [ ]:
df_forward[["Position", "Jersey Number"]].groupby('Position').agg(lambda x: x.value_counts().index[0])

Jersey Number
Position               
CF                 17.0
LF                 10.0
LS                  9.0
LW                 11.0
RF                 10.0
RS                  9.0
RW                 11.0
ST                  9.0

# Мои выводы по распределению
Большинство нападающих предпочитают номер от 9 до 11, так как исторически номера для нападающих распределялись именно так. При этом распределение мультимодальное, есть мода в 19 номере, и если честно, я не знаю, как это объяснить.

Если смотреть по позициям, то самые популярные номера: 9-11, но вот у CF этот номер 17, и для меня это тоже загадка.

Так что самые популярные номера это 9-11 и 17-19.



---



---


# Есть ли за зависимость **силы удара** (ShotPower) от **ведущей ноги**? от **агрессивности** (Aggression)? 


In [ ]:
df_cop = df.copy(deep = True)[['ShotPower', 'Preferred Foot']].dropna()
df_cop['Preferred Foot'] = df_cop['Preferred Foot'].apply(lambda x: 0 if x == 'Right' else 1)
corr = spearmanr(df_cop['ShotPower'], df_cop['Preferred Foot'])
print("Значение корреляции Спирмена между силой удара и ведущей ногой: {}".format(corr[0]))

Значение корреляции Спирмена между силой удара и ведущей ногой: 0.06605136801640643


In [ ]:
df_cop['Preferred Foot'] = df_cop['Preferred Foot'].apply(lambda x: 'Right' if x == 0 else 'Left')
df_power = df_cop.groupby('Preferred Foot').agg('mean').\
                                            sort_values(by = 'ShotPower', 
                                                        ascending = False)

fig = go.Figure()
fig.add_trace(go.Bar(
    x=df_power.index,
    y=df_power['ShotPower'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_power['ShotPower'],
    orientation='v'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Зависимость силы удара от ведущей ноги')
fig.update_yaxes(title_text='Средняя сила удара')
fig.update_xaxes(title_text="Ведущая нога")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1000, height=800)
fig.show()

# Мои выводы по распределению
По значению корреляции можно сделать вывод, что зависимость слабая. По графику видно, что левши в среднем бьют чуть сильнее, но скорее это не связано напрямую с ведущей ногой, а связано с особенностями данных, тем более, что левшей не так много.


---


In [ ]:
df_cop = df.copy(deep = True)[['ShotPower', 'Aggression']].dropna()
corr = spearmanr(df_cop['ShotPower'], df_cop['Aggression'])
print("Значение корреляции Спирмена между силой удара и агрессивностью: {}".format(corr[0]))

Значение корреляции Спирмена между силой удара и агрессивностью: 0.4042351937017802


In [ ]:
df_power = df_cop.groupby('Aggression').agg('mean').\
                                            sort_values(by = 'ShotPower', 
                                                        ascending = False)

fig = go.Figure()
fig.add_trace(go.Bar(
    x=df_power.index,
    y=df_power['ShotPower'],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    text = df_power['ShotPower'],
    orientation='v'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Зависимость силы удара от агрессивности')
fig.update_yaxes(title_text='Средняя сила удара')
fig.update_xaxes(title_text="Агрессивность")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1500, height=800)
fig.show()

# Мои выводы по распределению
1. Люди со слабой агрессивностью бьют очень слабо, но начиная с уровня агрессивности 25 идёт резкий взлёт силы удара до средних занчений.

2. Начиная с уровня агрессивности 25 идёт в целом медленный подъём уровня средней силы удара.

Статистическая зависимость явно отслеживается, что видно и по коэффициенту корреляции, и по графику. Есть ли фактическая связь? Наверное, небольшая, но есть, так как более агрессивным людям свойственна и бОльшая сила, и бОльшая резкость движений, что в целом влияет на силу удара.


---



---

# Найдите суммарную стоимость игроков в каждом клубе. Визуализируйте соотношение сумарной стоимости топ 10 клубов. 

In [ ]:
df_clubs = df[['Club', 'Value']].groupby('Club').agg('sum').sort_values(by = 'Value', ascending = False).head(10)

In [ ]:
df_clubs

Value
Club                            
Real Madrid          874425000.0
FC Barcelona         852600000.0
Manchester City      786555000.0
Juventus             704475000.0
FC Bayern München    679025000.0
Atlético Madrid      644525000.0
Paris Saint-Germain  625325000.0
Tottenham Hotspur    618450000.0
Chelsea              606815000.0
Manchester United    588850000.0

In [ ]:
# удачи...
fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_clubs.index[::-1],
    x=df_clubs['Value'][::-1],
    name = 'Топ-10 самых дорогих клубов мира по сумме стоимости игроков',
    orientation='h',
))
configure_plotly_browser_state()
fig.update_layout(title_text='Топ-10 самых дорогих клубов мира по сумме стоимости игроков')
fig.update_xaxes(title_text='Суммарная стоимость игроков (В евро)/')
fig.update_yaxes(title_text="Клуб")
fig.update_layout(font_size = 16)
fig.update_layout(width=1300, height=800)
fig.show()

# Мои выводы по распределению
У топ-клубов -- наибольшая стоимость футболистов, всё логично. Но даже здесь Реал и Барса по стоимости превышают МЮ и Челси почти в полтора раза. 
А потом они придумали Суперлигу...



---



---


# Есть ли зависимость между продолжительностью контракта игрока и его стоимость? 

(Сначала исследую зависимость стоимость от того, в каком году заканчивается контракт)


Моя гипотеза в том, что эта зависимость существует, так как если контракт скоро истекает, то его можно взять дешевле. И ещё более крутым игрокам чаще предлагают долгосрочные контракты.

Для проверки гипотезы я выведу среднюю стоимость игроков с известным годом контракта.

In [ ]:
df_contract = df[['Contract Valid Until', 'Value']]
df_mean_contract = df_contract.groupby('Contract Valid Until').agg('mean')

In [ ]:
fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_mean_contract.index,
    x=df_mean_contract['Value'],
    name = 'Зависимость цены игрока от года окончания его контракта',
    orientation='h',
))
configure_plotly_browser_state()
fig.update_layout(title_text='Зависимость цены игрока от года окончания его контракта')
fig.update_xaxes(title_text='Средняя стоимость игроков')
fig.update_yaxes(title_text="Год окончания контракта")
fig.update_layout(font_size = 16)
fig.update_layout(width=1300, height=800)
fig.show()

# Мои выводы
Да, действительно от года конца контракта есть зависимость. Чем раньше он закончится, тем меньше стоимость игрока, так как в скором времени он вообще станет бесплатным.



---



Теперь исследуем продолжительность контракта. Создадим колонку 'Long', которая будет отражать текущую длительность нахождения человека в клубе. 
За дату перехода в клуб отвечает колонка 'Joined', за год окончания контракта - 'Contract Valid Until'. Подсчитаем просто как разницу годов.

In [ ]:
df_long = df[['Contract Valid Until', 'Value', 'Joined']].replace('nan', np.nan).dropna()

df_long['Long'] = df_long['Contract Valid Until'].astype(int) - df_long['Joined'].astype(int)

df_long = df_long[['Value', 'Long']]

In [ ]:
df_long = df_long.groupby('Long').agg('mean')

fig = go.Figure()
fig.add_trace(go.Bar(
    x=df_long.index,
    y=df_long['Value'],
    name = 'Распределение стоимости игрока от продолжительности контракта ',
    text = df_long['Value'],
    orientation='v'
))
configure_plotly_browser_state()
fig.update_layout(title_text='Распределение стоимости игрока от продолжительности контракта')
fig.update_yaxes(title_text='Средняя стоимость игрока')
fig.update_xaxes(title_text="Продолжительность контракта")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1500, height=800)
fig.show()

# Мои выводы

Статистическая зависимость действительно наблюдается. Это связано с тем, что чем лучше выступает игрок, тем более заинтересован в продлении контракта с ним клуб

Но начиная с 16 лет нахождения в клубе наступает резкий спад, так как игроки только стареют, а 16 лет - это целая карьера. Поэтому спрос на игроков резко падает, и поэтому цена на футболистов-долгожителей маленькая. Яркое исключение - Месси.



---



---



---



# В какой год будет больше всего свободных игроков на рынке (исходя из этих данных)? визуализируйте зависимость 

Нужная колонка - 'Contract Valid Until'

In [ ]:
df_free = df['Contract Valid Until'].value_counts().sort_index()
mask = ['blue'] * 9
mask[int(df_free.idxmax()) - 2018] = "red"

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_free.values,
    x=df_free.index,
    marker_color = mask,
    text = df_free.values,
    orientation='v',
))
configure_plotly_browser_state()
fig.update_layout(title_text='Поиск года, когда будет больше всего свободных игроков')
fig.update_xaxes(title_text='Год окончания контракта')
fig.update_yaxes(title_text="Количество игроков")
fig.update_traces(textposition='outside')
fig.update_layout(font_size = 16)
fig.update_layout(width=1300, height=800)
fig.show()

# Мои выводы
У большинства игроков в игре контракты заканчиваются в 2019 году. Выделено красным.
В 2020 и 2021 году тоже заканчиваются контракты у многих игроков, а в остальные года - значительно меньше. Сверхдолгосрочные контракты вообще у единиц.



---



---



---



# Есть ли зависмость потенциала (Potential) игрока от возраста? Всегда ли молодые игроки обладают большим потенциалом? 

Моя гипотеза состоит в том, что у молодых игроков потенциал выше, так как FIFA рисует молодёжи по дефолту потенциал около 70. И в этом они правы, так как понять, кто станет звездой - очень трудно.

In [ ]:
corr = spearmanr(df['Age'], df['Potential'])
print("Значение корреляции Спирмена: {}".format(corr[0]))

Значение корреляции Спирмена: -0.2633670218601628


In [ ]:
df_potential = df[['Potential', 'Age']]
df_potential = df_potential.groupby('Age').agg('mean')

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_potential['Potential'],
    x=df_potential.index,
    marker_color = 'blue',
    name = "Распределение",
    text = df_potential['Potential'],
    orientation = 'v'
))


configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость потенциала игрока от его возраста")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_xaxes(title_text="Возраст игрока")
fig.update_yaxes(title_text="Средний потенциал по этому возрасту")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы
Зависимость наблюдается и по графику, и по значению коэффициента корреляции. Объяснение здесь такое: старым игрокам никто не рисует потенциал намного больше, чем его ТС. А вот любому 17-летнему игроку, который попадает по мячу, смело рисуют +10-+15 к его потенциалу. Что в принципе естественно.


---




In [ ]:
fig = go.Figure()

x = np.arange(16, 22, 1)
for el in x:
  fig.add_trace(go.Box(y=df[df['Age'] == el]['Potential'], name = "Потенциал для возраста {}".format(el)))


configure_plotly_browser_state()
fig.update_layout(title_text= 'Распределение потенциала по возрастам')
fig.update_xaxes(title_text='Возраст')
fig.update_yaxes(title_text="Потенциал")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы
На этом графике видно, что в принципе всем молодым вне зависимости от конкретного возраста (17-21) рисуют примерно одинаковый потенциал.
И также видно, что, например, 16-летним вообще всем рисуют потенциал > 66, но в целом нижний квантиль для всех возрастов 69-70, то есть у 75% игроков действительно завышенный потенциал. Но есть и небольшое количество футболистов, у которых небольшой потенциал, но это скорее исключение из правила.



---



---



---



# Есть ли зависимость рейтинга игрока (Overall) от возраста? Когда у игроков "пик" карьеры? Игроков какого возраста больше всего с рейтингом 90+?  

Моя гипотеза состоит в том, что зависимость между рейтингом и возрастом существует: у молодых он маленький, у людей около 30 лет - максимальный, затем идёт спад.

In [ ]:
corr = spearmanr(df['Age'], df['Overall'])
print("Значение корреляции Спирмена для возраста и общего скилла: {}".format(corr[0]))

Значение корреляции Спирмена для возраста и общего скилла: 0.48309109339717193


In [ ]:
df_overall = df[['Overall', 'Age']]
df_overall = df_overall.groupby('Age').agg('mean')

fig = go.Figure()
fig.add_trace(go.Bar(
    y=df_overall['Overall'],
    x=df_overall.index,
    marker_color = 'blue',
    name = "Распределение",
    text = df_overall['Overall'],
    orientation = 'v'
))


configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость уровня игрока от его возраста")
fig.update_traces(texttemplate='%{text:.3s}', textposition='outside')
fig.update_xaxes(title_text="Возраст игрока")
fig.update_yaxes(title_text="Средний уровень по этому возрасту")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

In [ ]:
# Стало интересно, что за фрик 45-летний...
df[df['Age'] == 45]

ID      Name  Age  ... GKPositioning GKReflexes Release Clause
4741  140029  O. Pérez   45  ...          73.0       74.0          €272K

[1 rows x 88 columns]

# Мои выводы
График подтверждает мои мысли, которые я высказывал вначале: пик формы приходится примерно на 30 лет. По графику у молодых ребят средние способности около 55 (и ПС около 70)))), затем уже идёт рост по 2-3 пункта в год. К 27 годам рост замедляется, и футболист попадает на свой пик: от 28 до 34 лет. Затем идёт уже спад, но не такой яркий, как взлёт в начале карьеры, что связано с тем, что физический спад компенсируются более крутыми психологическими показателями и лучшими техническими скиллами. 

Ну а этот Перец из Пачуки с коротким пасом 26 испортил всю картину (


---



---



---




# Насколько средняя зарплата (Wage) игроков с рейтингом (Overall) 90+ больше средней зарплаты с рейтингом [80 - 90]? Визуализируйте возможную зависимость

Логично, что выше, но интересно, на сколько, ведь разница в рейтинге это по сути отличие отличного игрока от игрока мирового уровня (условно, Зинченко, Уокер - отличные футболисты, но звезда - все равно Де Брюйне) 

In [ ]:
skillmax = df[df['Overall'] > 90]['Wage'].mean()
skillmin = df[(df['Overall'] >= 80) & (df['Overall'] <= 90)]['Wage'].mean()
print("Средняя зарплата 90+: {}".format(skillmax))
print("Средняя зарплата 80-90: {}".format(skillmin))

print("Первые получают больше в {} раз".format(skillmax / skillmin))

Средняя зарплата 90+: 385555.55555555556
Средняя зарплата 80-90: 83582.41758241758
Первые получают больше в 4.6128787214771965 раз


In [ ]:
fig = go.Figure()

fig.add_trace(go.Box(y=df[(df['Overall'] >= 80) & (df['Overall'] <= 90)]['Wage'], name = "Общий уровень 80-90"))
fig.add_trace(go.Box(y=df[df['Overall'] > 90]['Wage'], name = "Общий уровень 90+"))


configure_plotly_browser_state()
fig.update_layout(title_text= 'Зависимость зарплаты от общего уровня')
fig.update_xaxes(title_text='Общий уровень')
fig.update_yaxes(title_text="Зарплата")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы
Видно, что футболисты с рейтингом 90+ получают в 3-4 раза больше, чем футболисты с рейтингом 80-90. Минимум зарплат у 90+ - 290 тысяч, тогда как upper fence у 80-90 - 230к, то есть разница космическая.



---


In [ ]:
x = np.arange(80, 95, 1)

y = []
for el in x:
  y.append(df[df['Overall'] == el]['Wage'].mean())

df_wage = pd.DataFrame(y, index = x, columns = ['Wage'])


fig = px.scatter(df_wage, x= df_wage.index, y="Wage", trendline="lowess", size = [2] * 15)
configure_plotly_browser_state()
fig.update_layout(title_text="Зависимость зарплаты от общего скилла")
fig.update_xaxes(title_text="Уровень игрока")
fig.update_yaxes(title_text="Средняя зарплата для такого скилла")
fig.update_layout(font_size = 16)
fig.update_layout(width=1400, height=800)
fig.show()

# Мои выводы
График показывает квадратичную зависимость зарплаты от скилла. Из-за этого кластер 90+ такой богатый.



---



---

